In [42]:
import pandas as pd
import os
import librosa
import numpy as np
import scipy
import re
import math


#Pickling
from six.moves import cPickle as pickle

# Normalizer
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import scale
#HTTP
import requests
import json

import matplotlib.pyplot as plt
import matplotlib.style as ms
import librosa.display
import IPython.display as ipd
import seaborn
ms.use('seaborn-muted')
%matplotlib inline

x_train = []
y_train = []
x_test = []
y_test = []
no_alignment_file = [4764]

In [2]:
def extract_patterns(data,extract=False):
    if(extract):
        patterns = {}
        for index, row in data.iterrows():
            patterns[row['index']] = set(get_pattern([row['text']])[0].values())
            print('Extracted pattern from '+ row['index'] + ' index:'+ str(index))
            print('Size: ', len(patterns[row['index']]), 'Patterns size', len(patterns))
        try:
            print('Saving Pickle')
            with open('pickles/patterns/pattern.pickle','wb') as f:
                save = {
                    'patterns' : patterns
                }
                pickle.dump(save,f,pickle.HIGHEST_PROTOCOL)
                print('Successfully saved in pattern.pickle')
                return patterns
        except Exception as e:
            print('Unable to save data to pickle', e)
            print('Patterns probably not saved.')
            return patterns
    else:
        try:
            with open('pickles/patterns/pattern.pickle','rb') as f:
                save = pickle.load(f)
                patterns = save['patterns']
                del save
                returning = {}
                for key in list(data['index']):
                    returning[key] = patterns[key]
                return returning
        except Exception as e:
            print('Error loading base datasets pickle: ', e)

def get_pattern(text):
    text = json.dumps(text)
    url = 'http://192.168.2.101:7878/api/get_patt'
    data = dict(input_tweets = text)
    resp = requests.post(url=url, data=data)
    r = json.loads(resp.text)
    return map(lambda x: x['pattern'],r)
    
def get_deep_emotion(text):
    text = json.dumps(text)
    url = 'http://192.168.2.101:7878/api/get_emo'
    data = dict(input_tweets = text)
    resp = requests.post(url=url, data=data)
    r = json.loads(resp.text)
    return r

def get_gender(text):
    text = text[len(text)-4]
    if('F' in text):
        return 'F'
    elif('M' in text):
        return 'M'
    else:
        return 'N/A'
    
def get_word_segments(align_file):
    segments = []
    try:
        with open(align_file,'r') as openFile:
            read_lines = openFile.readlines()
            lines = read_lines[1:len(read_lines)-1]
            for line in lines:
                splitted = line.split()
                segments.append({'sf': splitted[0], 'ef':splitted[1],'seg_scr':splitted[2],'word':splitted[3]})
    except Exception as e:
        print('Problem with file ',align_file)
    return segments

def clean_text(text):
    punct_str = '!"#$%&()*+,-./:;<=>?@\\^_`{|}~«»“…‘”\t'
    for p in punct_str:
        text = text.replace(p,' ')
    text = re.sub(' +', ' ', text)
    return text.lower().strip()

def play_audio(filename):
    y, sr = librosa.load(filename)
    return ipd.Audio(data=y,rate=sr)

# def play_audio(y,sr,start,end):
#     return ipd.Audio(data= y[start:end], rate=sr)
    
def extract_patterns(data,extract=False):
    if(extract):
        patterns = {}
        for index, row in data.iterrows():
            patterns[row['index']] = set(get_pattern([row['text']])[0].values())
            print('Extracted pattern from '+ row['index'] + ' index:'+ str(index))
            print('Size: ', len(patterns[row['index']]), 'Patterns size', len(patterns))
        try:
            print('Saving Pickle')
            with open('pickles/patterns/pattern.pickle','wb') as f:
                save = {
                    'patterns' : patterns
                }
                pickle.dump(save,f,pickle.HIGHEST_PROTOCOL)
                print('Successfully saved in pattern.pickle')
                return patterns
        except Exception as e:
            print('Unable to save data to pickle', e)
            print('Patterns probably not saved.')
            return patterns
    else:
        try:
            with open('pickles/patterns/pattern.pickle','rb') as f:
                save = pickle.load(f)
                patterns = save['patterns']
                del save
                returning = {}
                for key in list(data['index']):
                    returning[key] = patterns[key]
                return returning
        except Exception as e:
            print('Error loading base datasets pickle: ', e)
            
def filter_word_count(data, n_count):
    return data[list(map(lambda x: len(x.split(' ')) >= n_count,data['text']))]

def remove_empty_patterns(data,patterns):
    empty_patterns = [k for k, v in patterns.items() if len(v) < 1]
    patterns = { k:v for k, v in patterns.items() if len(v) > 1 }
    data = filter(lambda x: x[1]['index'] not in empty_patterns ,data.iterrows())
    data = pd.DataFrame.from_items(data).T
    return data,patterns

# Feature Extractors

In [50]:
def get_mfcc(y,sr,se_tup,n_mfcc=20):
    mfcc = librosa.feature.mfcc(y=y[se_tup[0]:se_tup[1]],sr=sr, n_mfcc=n_mfcc)
    mfcc = np.mean(mfcc,axis=1)
    return mfcc

def scale_features(x_train, x_test):
    scaler = MinMaxScaler(feature_range=(-1, 1))
    scaled_x_train = scaler.fit_transform(x_train)
#     print(scaled_x_train.min(axis=0))
#     print(scaled_x_train.max(axis=0))
    scaled_x_test = scaler.fit_transform(x_test)
    return scaled_x_train,scaled_x_test

def get_rmse(y,se_tup):
    return np.sqrt(np.mean(y[se_tup[0]:se_tup[1]]**2))

def extract_features(y,sr, se_tup):
    results = [
        get_mfcc(y,sr,se_tup),
        get_rmse(y,se_tup),
    ]
    return results
    
                

In [85]:
def load_data(word_count,emotional_mapping):
    # full = generate_IEMOCAP_df()
    data = pd.read_csv('data/IEMOCAP_sentences.csv',index_col=0)
    data['emotion_code'] = data['emotion'].map( emotional_mapping ).astype(int)
    # Take away fear, surprise,disgust, xxx and others. Not enough data
    data = data[data.emotion_code < 4]
    #Remove rows that don't have Alignment file
#     data = data.drop(no_alignment_file)
    # Clean Transcripts
    data['text'] = data['text'].apply(clean_text)
    # Filter Word Count
    data = filter_word_count(data, word_count)
    patterns = extract_patterns(data)
    data,patterns = remove_empty_patterns(data,patterns)
    return data,patterns

def get_word_coordinate(word_segments,transcript, y_size):
    word_data = []
    start_data = []
    end_data = []
    silence = ['<sil>']
    actions = ['++garbage++','++breathing++', '++laughter++','++lipsmack++']
    if(len(word_segments) > 0 ):
        frames = list(map(lambda x: (x['sf'],x['ef']),word_segments))
        frame_size = int(frames[len(frames)-1][1])
        rate = y_size / frame_size
        word_segments.pop()
        word_segments.pop(0)
        text_tokens = transcript.split(' ')
        token_index = 0
        for wordsg in word_segments:
            word = wordsg['word'].lower().split('(')[0]
            if(word in silence):
                'There is a silence here'
            elif(word in actions):
                action = word
                token_index += 1
            else:
                word_data.append(word)
                start_data.append(math.floor(int(wordsg['sf'])* rate))
                end_data.append(math.ceil(int(wordsg['ef'])* rate))
                
                if(word != text_tokens[token_index]):
                    print('ERROR')
                    print('Expected', text_tokens[token_index])
                    print('Found', word)
                    return None
                token_index +=1
        return [word_data,start_data,end_data]
    return None

def matchForcedAlign(patt,parsedData):
    wild_card = '.+'
    i = 0
    initWildCardCount = 0
    endWildCardCount = 0
    wordCount = 0
    word_index = []
    transcript = parsedData[0]
    passedWord = False
    pattern_tokens = patt.split(' ')
    for token in pattern_tokens:
        if(token == wild_card):
            if(passedWord):
                endWildCardCount += 1
                # TODO: Fix instance of [con_w wild_card con_w]
            else:
                initWildCardCount += 1
        else:
            passedWord = True
            wordCount += 1
            if word_index == []:
                word_index = [i for i, e in enumerate(transcript) if e == token]
    results = []
    index_removal = []
    for index in word_index:
        if((index - initWildCardCount) >= 0 and (index + wordCount - 1 + endWildCardCount) < len(transcript)):
            index_result = [(-1,-1),(-1,-1),(-1,-1)]
            if(initWildCardCount > 0):
                index_result[0] = (parsedData[1][index-initWildCardCount],parsedData[2][index - 1])
            if(endWildCardCount > 0):
                index_result[2] = (parsedData[1][index + wordCount],parsedData[2][index+ wordCount - 1 + endWildCardCount])
            index_result[1] = (parsedData[1][index],parsedData[2][index + wordCount - 1])
            results.append(index_result)
        else:
            index_removal.append(index)
    for index in index_removal:
        word_index.remove(index)
    return word_index, results, [initWildCardCount,wordCount,endWildCardCount]


In [51]:
emotional_mapping = {'ang': 0, 'sad': 1, 'hap': 2, 'neu': 3,'fru': 4,'exc': 5,'fea': 6,'sur': 7,'dis': 8, 'xxx':9,'oth':10}
data,patterns = load_data(3,emotional_mapping)
data.groupby('emotion').count()['index']


Error loading base datasets pickle:  'Ses01F_impro02_F007'


AttributeError: 'NoneType' object has no attribute 'items'

In [94]:
extractFeatures = True
exit = False
feature_table = None
if(extractFeatures):
    wcards_b = False
    connectw_b = False
    all_patt = True
    feature_table = {}

    for pattern_name in patterns:
        row = data[data['index'] == pattern_name]
        emotion = row.emotion.values[0]
        wav_path = row.wav_path.values[0]
        align_path = row.alignment_path.values[0]
        segments = get_word_segments(align_path)
        transcript = row.text.values[0]
        y,sr = librosa.load(wav_path)
        parsedData = get_word_coordinate(segments,transcript,len(y))
        for patt in patterns[pattern_name]: 
            word_index, results, counts = matchForcedAlign(patt,parsedData)
            features_vect = []
            for index, result in enumerate(results):
                if(all_patt):
                    x_temp = result[0][0]
                    y_temp = result[2][1]
                    if(x_temp == -1):
                        x_temp= result[1][0]
                    if(y_temp == -1):
                        y_temp = result[1][1]
    
                    all_patt_feature = extract_features(y,sr,(x_temp,y_temp))
                    features_vect.append(all_patt_feature)
                if(wcards_b):
                    if(result[0][0] != -1 and result[2][0] != -1):
                        temp_y = np.concatenate([y[result[0][0]:result[0][1]] , y[result[2][0]:result[2][1]]])
                        wc_feat = extract_features(temp_y,sr,(0,len(temp_y)-1))
                        features_vect.append(wc_feat)
                    else:
                        if(result[0][0] != -1):
                            i_wc_i = result[0]
                            i_wc_feat = extract_features(y,sr,i_wc_i)
                            features_vect.append(i_wc_feat)
                        if(result[2][0] != -1):
                            e_wc_i = result[2]
                            e_wc_feat = extract_features(y,sr,e_wc_i)
                            features_vect.append(e_wc_feat)
                if(connectw_b):
                    cw_i = result[1]
                    cw_feat = extract_features(y,sr,cw_i)
                    features_vect.append(cw_feat)
            if(len(results) > 1):
                print('MORE THAN ONE',results)
                print(features_vect)
                break
                #TODO: Just considering the first find in the Pattern Detected 
            print('Extracted feature from pattern',patt,'in recording',pattern_name)
            for index,features in enumerate(features_vect):
                feature_table[(pattern_name, patt,index)] = features
            
    try:
        print('Saving Pickle')
        with open('pickles/patterns/pattern_features4emo.pickle','wb') as f:
            save = {
                'feature_table' : feature_table
            }
            pickle.dump(save,f,pickle.HIGHEST_PROTOCOL)
            print('Successfully saved in pattern_features.pickle')
    except Exception as e:
        print('Unable to save data to pickle', e)
else:
    try:
        with open('pickles/patterns/pattern_features.pickle','rb') as f:
            save = pickle.load(f)
            feature_table = save['feature_table']
            del save
    except Exception as e:
        print('Error loading pattern features pickle: ', e)



Extracted feature from pattern .+ .+ a in recording Ses01F_impro01_F002
Extracted feature from pattern a .+ in recording Ses01F_impro01_F002
Extracted feature from pattern .+ a in recording Ses01F_impro01_F002
Extracted feature from pattern .+ there in recording Ses01F_impro01_F002
Extracted feature from pattern is .+ a in recording Ses01F_impro01_F002
Extracted feature from pattern .+ a .+ in recording Ses01F_impro01_F002
Extracted feature from pattern .+ problem in recording Ses01F_impro01_F002
Extracted feature from pattern is there .+ in recording Ses01F_impro01_F002
Extracted feature from pattern there .+ in recording Ses01F_impro01_F002
Extracted feature from pattern is .+ in recording Ses01F_impro01_F002
Extracted feature from pattern there a .+ in recording Ses01F_impro01_F002
Extracted feature from pattern .+ it in recording Ses01F_impro01_F005
Extracted feature from pattern .+ let in recording Ses01F_impro01_F005
Extracted feature from pattern let .+ in recording Ses01F_impro

Extracted feature from pattern .+ .+ to in recording Ses01F_impro02_F003
Extracted feature from pattern to make .+ in recording Ses01F_impro02_F003
Extracted feature from pattern you .+ .+ in recording Ses01F_impro02_F003
Extracted feature from pattern guess .+ in recording Ses01F_impro02_F003
Extracted feature from pattern you .+ in recording Ses01F_impro02_F003
Extracted feature from pattern know .+ in recording Ses01F_impro02_F003
Extracted feature from pattern .+ to make in recording Ses01F_impro02_F003
Extracted feature from pattern .+ .+ you in recording Ses01F_impro02_F003
Extracted feature from pattern i guess .+ in recording Ses01F_impro02_F003
Extracted feature from pattern everybody .+ in recording Ses01F_impro02_F003
Extracted feature from pattern .+ you .+ in recording Ses01F_impro02_F003
Extracted feature from pattern to .+ in recording Ses01F_impro02_F003
Extracted feature from pattern i .+ in recording Ses01F_impro02_F003
Extracted feature from pattern .+ know in record

Extracted feature from pattern .+ have .+ in recording Ses01F_impro02_F016
Extracted feature from pattern .+ have to in recording Ses01F_impro02_F016
Extracted feature from pattern to .+ .+ in recording Ses01F_impro02_F016
Extracted feature from pattern to .+ in recording Ses01F_impro02_F016
Extracted feature from pattern .+ have in recording Ses01F_impro02_F016
Extracted feature from pattern i .+ in recording Ses01F_impro02_F016
Extracted feature from pattern .+ to .+ in recording Ses01F_impro02_F016
Extracted feature from pattern find .+ in recording Ses01F_impro02_F016
Extracted feature from pattern have to .+ in recording Ses01F_impro02_F016
Extracted feature from pattern .+ find in recording Ses01F_impro02_F016
Extracted feature from pattern have .+ in recording Ses01F_impro02_F016
Extracted feature from pattern to find .+ in recording Ses01F_impro02_F016
Extracted feature from pattern .+ to in recording Ses01F_impro02_F016
Extracted feature from pattern .+ .+ to in recording Ses0

Extracted feature from pattern .+ okay in recording Ses01F_impro02_M005
MORE THAN ONE [[(-1, -1), (17268, 19705), (19925, 21697)], [(-1, -1), (47156, 49593), (49813, 51142)]]
[[array([-431.46448332,  197.14614973,  -48.12456771,   50.14664638,
        -30.17073216,   27.88630035,  -16.06745556,    0.43812373,
          9.49868518,   -7.44089988,    9.24225985,    0.94626685,
         20.40226298,  -10.43828115,    1.80474471,   -4.57713133,
         -1.68541295,    2.51736012,  -16.11884894,    8.17106199]), 0.009281643], [array([-4.09333719e+02,  2.05954723e+02, -4.18930558e+01,  4.60841262e+01,
       -2.52029037e+01,  1.38193790e+01, -1.61462687e+01, -2.73736532e+00,
        7.34756457e+00, -2.20148529e+01,  1.21943875e+00,  1.54267220e+00,
        1.22921919e+01, -2.21335678e+00,  3.98250008e+00, -2.19580440e-01,
       -5.22775371e+00, -1.63777622e+00, -1.10719089e+01,  3.73514903e+00]), 0.014181778]]
Extracted feature from pattern .+ see in recording Ses01F_impro02_M009
Extracted

Extracted feature from pattern it .+ in recording Ses01F_impro02_M013
Extracted feature from pattern .+ just in recording Ses01F_impro02_M013
Extracted feature from pattern i .+ in recording Ses01F_impro02_M013
Extracted feature from pattern .+ know in recording Ses01F_impro02_M013
Extracted feature from pattern .+ to .+ in recording Ses01F_impro02_M013
Extracted feature from pattern to .+ it in recording Ses01F_impro02_M013
Extracted feature from pattern .+ how in recording Ses01F_impro02_M013
Extracted feature from pattern .+ do in recording Ses01F_impro02_M013
Extracted feature from pattern just .+ in recording Ses01F_impro02_M013
Extracted feature from pattern .+ do .+ in recording Ses01F_impro02_M013
Extracted feature from pattern .+ .+ a in recording Ses01F_impro02_M014
Extracted feature from pattern a .+ in recording Ses01F_impro02_M014
Extracted feature from pattern .+ a in recording Ses01F_impro02_M014
Extracted feature from pattern baby .+ in recording Ses01F_impro02_M014
Ext

...

Extracted feature from pattern far .+ in recording Ses05M_script03_2_F035
Extracted feature from pattern try .+ in recording Ses05M_script03_2_F035
Extracted feature from pattern far too .+ in recording Ses05M_script03_2_F035
Extracted feature from pattern to .+ .+ in recording Ses05M_script03_2_F035
Extracted feature from pattern are .+ too in recording Ses05M_script03_2_F035
Extracted feature from pattern .+ to in recording Ses05M_script03_2_F035
Extracted feature from pattern .+ .+ to in recording Ses05M_script03_2_F035
Extracted feature from pattern you .+ .+ in recording Ses05M_script03_2_F035
Extracted feature from pattern .+ too in recording Ses05M_script03_2_F035
Extracted feature from pattern to .+ yourself in recording Ses05M_script03_2_F035
Extracted feature from pattern you .+ in recording Ses05M_script03_2_F035
Extracted feature from pattern are .+ .+ in recording Ses05M_script03_2_F035
Extracted feature from pattern .+ are .+ in recording Ses05M_script03_2_F035
Extracted 

Extracted feature from pattern too .+ in recording Ses05M_script03_2_M009
Extracted feature from pattern me too .+ in recording Ses05M_script03_2_M009
Extracted feature from pattern .+ too in recording Ses05M_script03_2_M009
Extracted feature from pattern me .+ in recording Ses05M_script03_2_M009
Extracted feature from pattern bored .+ in recording Ses05M_script03_2_M009
Extracted feature from pattern me .+ .+ in recording Ses05M_script03_2_M009
Extracted feature from pattern .+ you want in recording Ses05M_script03_2_M010
Extracted feature from pattern do .+ in recording Ses05M_script03_2_M010
Extracted feature from pattern .+ you .+ in recording Ses05M_script03_2_M010
Extracted feature from pattern .+ some in recording Ses05M_script03_2_M010
Extracted feature from pattern do you .+ in recording Ses05M_script03_2_M010
Extracted feature from pattern .+ you in recording Ses05M_script03_2_M010
Extracted feature from pattern some .+ in recording Ses05M_script03_2_M010
Extracted feature fr

MORE THAN ONE [[(76706, 91739), (91959, 94170), (-1, -1)], [(129317, 136392), (136612, 139708), (-1, -1)], [(152528, 160045), (160265, 162034), (-1, -1)]]
[[array([-272.64972848,  160.14045013,  -41.2417244 ,   52.45315431,
        -34.08573624,    8.56961024,   -1.04466695,  -16.06614491,
         -6.5521449 ,  -11.38770361,    2.85219277,   -5.85191453,
          3.67288794,   -8.6518281 ,    1.08343906,   -2.10469257,
         -6.00420645,    0.86831281,   -8.06518941,    2.77004156]), 0.058703065], [array([-221.41498641,  146.27202219,  -69.71748155,   47.32418768,
        -29.90960316,   -1.19140089,   -6.52655695,  -17.2207636 ,
         -8.42606441,   -6.47201215,   17.2176874 ,   -2.33212705,
          3.3100636 ,   -7.13587545,   -3.43410802,   -2.12979938,
        -10.10262511,   -3.60410944,  -12.03526619,   -1.9642088 ]), 0.09453375], [array([-266.2385344 ,  181.39016517,  -72.32471772,   57.72004533,
        -17.6835772 ,   -8.64378008,  -12.084545  ,   -5.76311178,
      

Extracted feature from pattern .+ the .+ in recording Ses05M_script03_2_M033
Extracted feature from pattern .+ and in recording Ses05M_script03_2_M033
Extracted feature from pattern .+ very in recording Ses05M_script03_2_M033
Extracted feature from pattern .+ late in recording Ses05M_script03_2_M033
Extracted feature from pattern very .+ in recording Ses05M_script03_2_M033
Extracted feature from pattern and .+ in recording Ses05M_script03_2_M033
Extracted feature from pattern .+ people in recording Ses05M_script03_2_M034
Extracted feature from pattern .+ are .+ in recording Ses05M_script03_2_M034
Extracted feature from pattern .+ there in recording Ses05M_script03_2_M034
Extracted feature from pattern .+ i in recording Ses05M_script03_2_M034
Extracted feature from pattern well .+ in recording Ses05M_script03_2_M034
Extracted feature from pattern i .+ in recording Ses05M_script03_2_M034
Extracted feature from pattern people .+ in recording Ses05M_script03_2_M034
Extracted feature from p

MORE THAN ONE [[(-1, -1), (28129, 34774), (34995, 36768)], [(-1, -1), (48506, 54044), (54265, 55373)], [(-1, -1), (55593, 60467), (60688, 67776)]]
[[array([-171.19819742,  128.98385535,  -98.81234272,   61.26305138,
        -16.56493254,   -4.93238616,  -13.48861038,  -22.16122732,
         -8.94789121,  -15.71881714,   -1.46791093,   -7.31840133,
          0.651114  ,  -18.83587307,   -6.36688564,    3.8012197 ,
        -19.99064073,  -13.31532646,   -9.87654852,   -7.96566275]), 0.17910063], [array([-147.26837709,  128.09134296,  -65.23423468,   69.93380764,
        -24.016362  ,   -1.38827117,   -6.6695309 ,   -9.38565913,
        -15.88813877,  -29.83546579,  -19.64504661,  -10.8583989 ,
         11.97872061,  -22.33808413,   -7.0948644 ,    2.65848223,
        -13.29281765,   -0.3924355 ,   -7.52769751,   -8.54148516]), 0.21838696], [array([-119.29650821,  132.22486789,  -82.3635651 ,   56.34763838,
        -27.35017032,   -1.9379669 ,  -10.70423923,  -16.22319962,
         -0.760

In [92]:
# test = []
# for key, feature in feature_table.items():
#     print(key)
#     print(len(feature))
#     if(len(feature) < 1):
#         test = feature
#         break

feature_table

{('Ses01F_impro01_F002',
  '.+ .+ a',
  0): [array([-400.74855042,  163.25832925,  -32.90028138,   46.81928825,
          -18.41416636,   34.15479477,  -18.99048663,  -20.45046705,
           -6.51360778,   -7.63747739,    8.63177181,  -13.39743771,
            9.85040793,    3.31526127,    5.27219723,   -7.18319442,
           -4.31411007,    7.85033307,  -10.39079854,    1.14501905]), 0.021823993],
 ('Ses01F_impro01_F002',
  '.+ a',
  0): [array([-366.63874256,  174.98027421,  -41.22733297,   49.04114688,
          -19.86539146,   36.61814686,  -23.61110969,  -28.18169217,
          -10.03453155,   -5.87591808,    6.41670283,  -18.90171291,
            9.36670083,    3.65958789,    4.85740429,  -10.43336264,
           -0.64454113,    9.33649794,  -14.16162785,    1.9494998 ]), 0.025554834],
 ('Ses01F_impro01_F002',
  '.+ a .+',
  0): [array([-3.64798252e+02,  1.89837388e+02, -4.77086162e+01,  2.62997460e+01,
         -2.62000981e+01,  1.49948407e+01,  5.87922131e+00, -1.76665550e+01

In [68]:
test

[]

In [44]:
save = pd.read_pickle('pickles/patterns/pattern_features.pickle')
feature_table = save['feature_table']
del save

In [45]:
feature_table

{'Ses03M_impro08a_M019<PATTERN>.+ through': [[array([-4.81830820e+02,  1.59664409e+02, -1.80356637e+01,  7.09126990e+01,
          -4.05491026e-01,  2.12183166e+01, -5.26466949e+00, -3.26901914e+00,
           5.91250951e-01, -1.66887489e+01, -2.52675862e+00, -1.28656044e+01,
           5.81393301e+00, -1.25869640e+01, -4.65971371e+00,  4.40350179e+00,
          -1.48914836e+01, -3.94845510e+00, -3.99964658e-01, -1.38361262e+00]),
   0.010872793]],
 'Ses02M_impro07_M017<PATTERN>the .+ .+': [[array([-2.95594206e+02,  1.65361324e+02, -4.33112603e+01,  7.14592890e+01,
          -1.45175390e+01, -3.85889736e+00, -9.32373575e+00, -3.37130092e+00,
          -1.08837630e+01, -1.38149507e+01,  6.82918644e+00, -1.76816099e+01,
           1.70187227e+00, -1.23568934e+01,  2.86444252e-01,  6.59902428e+00,
          -1.40820941e+01,  4.23201859e-01, -7.98146460e+00, -4.76985522e+00]),
   0.0491465]],
 'Ses01M_impro03_F010<PATTERN>just .+': [[array([-196.27052816,   81.95566471,  -69.20609162,   82